In [55]:
!pip3 install numpy scipy umap-learn soundfile wav2clip

     |████████████████████████████████| 88 kB 4.2 MB/s eta 0:00:01
     |████████████████████████████████| 1.1 MB 16.9 MB/s eta 0:00:01
  Created wheel for umap-learn: filename=umap_learn-0.5.3-py3-none-any.whl size=82829 sha256=f670c0ffed1a4362146b033e2e246eb08c1b9cab99d1b836bf849e11e3e57791
  Stored in directory: /Users/nsingh1/Library/Caches/pip/wheels/f4/3e/1c/596d0a463d17475af648688443fa4846fef624d1390339e7e9
  Created wheel for pynndescent: filename=pynndescent-0.5.8-py3-none-any.whl size=55512 sha256=56f679366c2493ed16764f42a1ef0c3c4c1e17013f6e7839aa97b191a4c55587
  Stored in directory: /Users/nsingh1/Library/Caches/pip/wheels/b9/89/cc/59ab91ef5b21dc2ab3635528d7d227f49dfc9169905dcb959d
Successfully built umap-learn pynndescent


In [57]:
import os
import numpy
import soundfile
import scipy.signal
import wav2clip
import ipywidgets
import umap
from tqdm.auto import tqdm

In [20]:
w = ipywidgets.Dropdown(options=glob.glob("./*/"))
w

Dropdown(options=('./drum/', './vocal/'), value='./drum/')

In [72]:
f = w.value
with open(os.path.join(f, "samples.txt")) as infile:
    files = [os.path.join(f, file) for file in infile.read().splitlines()]
print("Will embed %d files." % len(files))

Will embed 1329 files.


In [ ]:
def embed_file(file, model):
    y, sr = soundfile.read(file)
    if len(y.shape) > 1:
        y = y.mean(axis=1)
    audio = scipy.signal.resample(y, int((len(y)/sr) * 16000)).astype(numpy.float32)
    return wav2clip.embed_audio(audio, model)

model = wav2clip.get_model()
embeddings = [embed_file(file, model) for file in tqdm(files)]

  0%|          | 0/1329 [00:00<?, ?it/s]

In [ ]:
all_embeddings = numpy.vstack([x[0] for x in embeddings])
t = umap.UMAP(
    n_components=2,
    min_dist=0.1,
    a=0.05,
    b=0.8,
    spread=10
)

coords = t.fit_transform(all_embeddings)
numpy.savetxt(os.path.join(f, "coords.txt"), coords, fmt="%.8f")